In [137]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [138]:
from lib import *
from fun import *

# Variables

In [139]:
cardinal_grouped_polygons = 100
root = "data/elevation_files/"
datafilename = "data/polygons_and_points.csv"

# Import data

In [140]:
df = pd.read_csv(datafilename)

# Build Marks Array

In [141]:
marks = np.linspace(0,len(df),int(len(df)/cardinal_grouped_polygons)).astype(int)
a = marks[:-1]
b = marks[1:]
marks = np.vstack((a,b))
marks = marks.transpose()

# Retrive elevations

In [142]:
errors_counter = 0
errors_list = []
points_counter = 0

for idxmarker,bornes in enumerate(marks[:]):
    start,end = bornes
    tempdf = df[start:end]
    some_points = tempdf[["long","lat"]].to_dict(orient = "split")["data"]
    
    try:
        
        tempdata = py3dep.elevation_bycoords(some_points,crs="epsg:4326")
        exportdf = tempdf.polygonid.to_frame().reset_index(drop=True)
        exportdf["elevation"] = tempdata
        
        tempfilename = root + "file_" + str(idxmarker).zfill(5) + "_from_" + str(start) + "_to_" + str(end) + ".csv"
        exportdf.to_csv(tempfilename,index = False)
        
        points_counter = points_counter + len(exportdf)
        progression = round(100*(points_counter / len(df))  ,  2)
        progression = str(progression) + "%"
    
    except:
        errors_list.append((idxmarker,bornes,tempdf))
        errors_counter = errors_counter + 1
        
    clear_output(wait=True)
    print("Elevation points computed so far : ",points_counter,"(",progression,") | errors : ",errors_counter)

Elevation points computed so far :  4998 ( 100.0% ) | errors :  0


In [130]:
pickle.dump( errors_list, open( root + "errors_list.p", "wb" ) )

# Compute average elevation by block group and save it to a json file

In [158]:
folderfiles = listdir(root)
filenames_list = [filename for filename in folderfiles if filename.endswith("csv") ]
list_of_dataframes = [pd.read_csv(root + tempfilename) for tempfilename in filenames_list]
elevation_df = pd.concat(list_of_dataframes)
elevation_dict = elevation_df.groupby("polygonid")["elevation"].mean().to_dict()

with open('data/polygons_elevation.json', 'w') as f:
    json.dump(elevation_dict, f)

# Afficher la map

In [202]:
shapefilename = "data/polygons/TG00CAGRP.shp"
elevation_json_name = 'data/polygons_elevation.json'

In [203]:
with open(elevation_json_name) as json_file:
    elevation_data = json.load(json_file)
    
blocks = fiona.open(shapefilename)
blocks_polygons = [shape(item["geometry"]) for item in blocks]

In [204]:
elevation_data = [(int(k),v) for k,v in elevation_data.items()]
polygondf = pd.DataFrame(elevation_data,columns=["polygonid","elevation"])
minval = min(polygondf.elevation)
maxval = max(polygondf.elevation)
polygondf["elevation_color"] = ColorMapper(minval,maxval,polygondf.elevation,"RdYlGn_r")

In [205]:
# creation du geojson
features = []

for rowid,others in polygondf.iterrows():
    temp_elevation = others["elevation"]
    temp_color = others["elevation_color"]
    temp_id = others["polygonid"]
    
    data = {}
    data["rowid"] = int(temp_id)
    data["fillcolor"] = str(temp_color)
    data["fill_opacity"] = 0.66
    data["color"] = "white"
    data["opacity"] = 0
    data["elevation"] = int(temp_elevation)
    
    feature = {"type":"Feature",
               "properties":data,
               "geometry":shapely.geometry.mapping(blocks_polygons[int(temp_id)])}
    
    features.append(feature)
    
final_geojson = {"type": "FeatureCollection","features" : features}

In [206]:
centroids_array = [(pp.centroid.xy[-1][-1],pp.centroid.xy[0][-1]) for pp in blocks_polygons]
barycentre = np.mean(centroids_array,axis=0)
m = folium.Map(location = barycentre, zoom_start= 6,width="66%",tiles="Cartodbdark_matter")

stylefun = lambda x: {'fillColor' : x['properties']['fillcolor'],
                      'fillOpacity' : x['properties']['fill_opacity'],
                     'color' : x['properties']['color'],
                     'opacity' : x['properties']['opacity']}

folium.GeoJson(data=final_geojson,
               style_function= stylefun,
               smooth_factor=1,
               tooltip=folium.features.GeoJsonTooltip(fields=["rowid","elevation"],
                                                      aliases=["Polygone ID : ","Elevation (meters) : "])).add_to(m)

In [207]:
m